# Authentication

In previous tutorials we focused on Control-M Workbench where authentication is not an issue. In real environments, authentication is necessary and it is essential to follow best practice to prevent a leak of sensitive information.

Authentication is needed to work with the backend of Control-M. The authentication is done by default at the creation of a `Workflow`. You can skip the initial authentication if, for example, you want to code a workflow without the intent of running it immediately.


## Environments

An `Environment` is an object passed to the `Workflow` during its construction. The environment defines the Control-M endpoint which is the endpoint where Automation API is installed, ehich is the same endpoint of Control-M/EM. When you create an environment you need to specify the credentials to be used during authentication and the `EnvironmentMode`

There are two methods of authentication used in Control-M: username+password and API key. When you construct an Environment, you can either specify a combination of username and password or an API key.

The `EnvironmentMode` serves to indicate if the backend is of type Control-M or Helix Control-M (Control-M SaaS). This is important since the backend APIs are slightly different. You can specify the mode in the constructor or use the static method `Environment.create_onprem()` or `Environment.create_saas()`

In [ ]:
# Examples of Environments
from ctm_python_client.core.workflow import *
from ctm_python_client.core.comm import *
from ctm_python_client.core.credential import *

# Create an environment for Control-M
my_environment = Environment('https://mymachine:8443/automation-api', username='user', password='password', mode=EnvironmentMode.ONPREM)

# which is the same:
# Note that OnPrem environment by default use the port 8443, if another port is used, you can specify it
my_environment = Environment.create_onprem('mymachine',username='user', password='password')

# Create an environment for Helix Control-M (SaaS)
my_environment = Environment.create_saas('https://mysaas-aapi/automation-api', api_key='myapikey')

# Create an environment to work with Control-M Workbench

# by default sets host to localhost and port to 8443
my_environment = Environment.create_workbench()

# If wokrbench is running on a remote machine, you can specify the host
my_environment = Environment.create_workbench(host='mymachine')

# In the case the port 8443 is mapped to another port (for example multiple instances of a workbench container), you can specify the port
my_environment = Environment.create_workbench(host='mymachine', port='8444')


workflow = Workflow(my_environment)



## Credentials

Control-M Python Client has an abstract class called `AbstractCredentials` with two methods: `get_username()` and `get_password()`. During authentication, those methods are called. 
If the authentication is done via API key, then only `get_password()` is called. 

When creating an Environment, you are required to provide Credentials. Control-M Python Client has some implementations which you can use.

- `SimpleCredentials`: Allows you provide the username and password directly during the creation. This is the least secure way of creating a credential since the password (or API key) is written in plain text.

- `InputPasswordCredentials`: Allows you to input the password during the execution of the code. This is more secure since the password is not in the document, but can disrupt automated process since it requires the intervention of the user.

- `KeyringCredentials` (in the `ext` package): Uses the keyring library which leverages secure backends from the operating system to store passwords.

- Your own: It would be impossible to code every way of getting passwords and you may have a vault service or a specific company policy for storing passwords. In this case, the easiest way is to implement your own credentials based on `AbstractCredentials`, and use your custom implementation as the credentials passed in the environment

In [ ]:

from ctm_python_client.core.workflow import *
from ctm_python_client.core.comm import *
from ctm_python_client.core.credential import *

# example of creating an workflow for Control-M with username and password:
workflow = Workflow(
    Environment.create_onprem('mhyHost', credentials=InputPasswordCredentials('myuser'))
)

# example of creating an workflow for Helix Control-M with an API key:
workflow = Workflow(
    Environment.create_saas('mhyHost', credentials=InputPasswordCredentials('token'))
)

# example with using Keyring
# make sure you have keyring installed: pip install keyring
from ctm_python_client.ext.credential import KeyringCredentials

# on a terminal run:
# keyring set servicename username 
# servicename is not used in the authentication but is useful to distinguish between multiple environments
# example:
# keyring set development myuser
# keyring set production myuser
# you also can do the same in python
import keyring
keyring.set_password('production', 'username')

# if using API key, the password is the key, and the username is not used, so you can put any value 
# that seems significant for you
# example:
# keyring set development tokenAdmin

